In [1]:
import numpy as np
import pandas as pd
import pickle

### Set the number of metadata columns in the sequencing data

In [2]:
num_metadata_cols = 3

### Load in read count data (Qiime2 taxa barplot csv files)

Samples were subsampled to 45,386 reads. Samples with less than this number of reads after DADA2 processing were removed.

In [3]:
df_seq_orig_species = pd.read_csv('data_files/species_counts_paired_43922.csv').set_index('index')

read_depth = df_seq_orig_species[df_seq_orig_species.columns[:-num_metadata_cols]].sum(axis=1)[0]

In [4]:
read_depth

43922

In [5]:
# This taxa was only in second batch of sequenced duodenum samples likely indicating it is a contaminant. It is removed because
# it interferes with a plot comparing saliva to duodenum samples.
df_seq_orig_species.drop(['D_0__Bacteria;D_1__Firmicutes;D_2__Bacilli;D_3__Bacillales;D_4__Paenibacillaceae;D_5__Paenibacillus;D_6__Paenibacillus darwinianus'], axis=1, inplace=True)

### Load in absolute abundance data (dPCR)

In [6]:
df_total_load = pd.read_excel('dPCR data/dPCR_total_loads_paired.xlsx', index_col=0)
df_total_load['Sample'] = df_total_load['Sample'].astype(str)

### Normalize concentration to the input volume

Several saliva volumes (weights) were missing. The volume was set to the average of all other saliva samples. <br>
Stool samples did not have weights. These were approximated. The median collected weight is 0.5g of stool and these are collected in Omnigut tubes which contain 2mL of fluid. 1/8 of this volume is used for extraction. Therefore the weight of stool was set to 0.5/8 (0.0625g).

In [7]:
## Filter out samples below LLOQ
df_total_load = df_total_load[df_total_load['Concentration']>2]

## Calculate Copies/mL
df_total_load['Copies/mL'] = df_total_load['Corrected Concentration']/df_total_load['Weight']
df_total_load['Log Copies/mL'] = np.log10(df_total_load['Copies/mL'])

### Calculate LOD in terms of absolute abundance and relative abundance, 95% confidence of the template being added to the sample (3 copy input)

In [8]:
# These samples were diluted before placing sample in library reaction due to inhibitors preventing amplification in undiluted sample
seq_dilutions = pd.read_csv('dPCR data/seq_dilution_paired.csv')
seq_dilutions_dict = {seq_dilutions['mod_ID'].iloc[i] : seq_dilutions['Seq_Dilution'].iloc[i] for i in range(len(seq_dilutions))}


# Create column to account for the fact that some samples were diluted before input into library prep reaction
df_total_load['Seq_Dilution'] = df_total_load.apply(lambda x: seq_dilutions_dict[x['mod_ID']], axis=1)

In [9]:
# uL added to the amplification rxn
seq_volume = 3.5
copy_input_threshold = 3

df_total_load['Copies in Amp Rxn'] = df_total_load['Concentration']*df_total_load['Dilution']/df_total_load['Seq_Dilution']*seq_volume
df_total_load['Rel. Abundance LOD (%)'] = copy_input_threshold/df_total_load['Copies in Amp Rxn']*100
df_total_load['Abs. Abundance LOD'] = df_total_load['Rel. Abundance LOD (%)']*df_total_load['Copies/mL']/100
df_total_load

Well  Concentration  PoissonConfMax  PoissonConfMin  Total  Positives  \
0   A05         1633.0          1666.0          1617.0  15457      11600   
1   B05         2093.0          2135.0          2073.0  15484      12871   
2   C05            6.1             7.5             5.5  17225         89   
3   D05            4.9             6.1             4.3  16945         70   
4   E05          571.0           585.0           563.0  15789       6068   
6   G05         2582.0          2634.0          2556.0  16087      14295   
8   A06         3290.0          3370.0          3250.0  14354      13478   
9   B06         2988.0          3054.0          2956.0  15026      13841   
10  C06         1612.0          1644.0          1596.0  15631      11660   
11  D06          651.0           668.0           643.0  15261       6489   
12  E06          154.0           161.0           150.0  15643       1916   
13  F06         3320.0          3390.0          3280.0  15130      14228   
15  H06         3050.0          3130.0          3020.0  13916      12879   
16  A07         1374.0          1404.0          1359.0  13580       9357   
17  B07          385.0           396.0           379.0  16380       4569   
19  D07         3740.0          3830.0          3700.0  15466      14823   
20  E07         1164.0          1189.0          1152.0  15335       9635   
0   A01          878.0           898.0           858.0  14732       7745   
1   B01          685.0           702.0           669.0  14865       6564   
2   C01          229.0           238.0           221.0  16076       2848   
3   D01         5810.0          6060.0          5590.0  13577      13480   
24  A04          663.0           679.0           647.0  15761       6787   
25  B04         1418.0          1447.0          1389.0  14972      10486   
26  C04         1001.0          1023.0           980.0  15088       8647   
27  D04          434.0           446.0           421.0  15930       4911   
28  E04          535.0           551.0           520.0  12812       4684   
30  G04          811.0           829.0           793.0  15561       7750   
31  H04          895.0           915.0           875.0  14848       7907   
32  A05          657.0           673.0           641.0  15284       6537   
33  B05          961.0           982.0           940.0  15238       8506   
34  C05         2283.0          2330.0          2237.0  14605      12507   
35  D05         1610.0          1643.0          1577.0  14344      10693   
37  F05         1279.0          1306.0          1252.0  14287       9469   
38  G05         1176.0          1201.0          1152.0  15113       9551   
40  A06         1614.0          1651.0          1577.0  11393       8503   
41  B06          383.0           396.0           371.0  12849       3573   
42  C06          443.0           456.0           429.0  13892       4356   
43  D06          935.0           957.0           912.0  12614       6914   
44  E06          541.0           557.0           526.0  12876       4749   
45  F06         1894.0          1936.0          1853.0  12449       9960   
46  G06          967.0           990.0           944.0  12630       7078   
47  H06          831.0           852.0           811.0  13101       6638   

          Primer Sample      Type  Dilution  Weight  Corrected Concentration  \
0   mod_Caporaso    387  Duodenum        10   0.397             1.633000e+06   
1   mod_Caporaso    388  Duodenum        10   1.105             2.093000e+06   
2   mod_Caporaso    390  Duodenum        10   0.555             6.100000e+03   
3   mod_Caporaso    391  Duodenum        10   0.308             4.900000e+03   
4   mod_Caporaso    392  Duodenum        10   0.365             5.710000e+05   
6   mod_Caporaso    409  Duodenum        10   1.825             2.582000e+06   
8   mod_Caporaso    417  Duodenum        10   0.279             3.290000e+06   
9   mod_Caporaso    418  Duodenum        10   0.202             2.988000e+06   
10  mod_Capora

### Generate dictionary for easier downstream conversion of relative to absolute abundances

In [10]:
total_load_dict = {df_total_load['mod_ID'].iloc[i] : df_total_load['Copies/mL'].iloc[i] for i in range(len(df_total_load))}
len(total_load_dict)

42

### Determine LOD thresholds. If LOD from poisson loading > LOD from sequencing use the sequencing value. LOD from sequencing is based on a 50% CV from replicates (Fig 2d from quant-seq paper).

In [11]:
seq_lloq = 7.115*(read_depth**(-0.556))

df_total_load['Rel. Abundance LOD (%) Corrected'] = df_total_load['Rel. Abundance LOD (%)'].where(df_total_load['Rel. Abundance LOD (%)']>seq_lloq, seq_lloq)

In [12]:
lod_dict = {df_total_load['mod_ID'].iloc[i] : df_total_load['Rel. Abundance LOD (%) Corrected'].iloc[i]*read_depth/100 for i in range(len(df_total_load))}

### Filter out samples without accurate total loads and store metadata in separate file

In [13]:
df_seq_samples = df_seq_orig_species[df_seq_orig_species.index.isin(total_load_dict.keys())][df_seq_orig_species.columns[:-1*num_metadata_cols]]

# This is num_metadata_cols-1 because we don't need the description column since it is already stored as the index
seq_metadata = df_seq_orig_species[df_seq_orig_species.columns[-1*(num_metadata_cols-1):]]
df_seq_samples

D_0__Archaea;D_1__Euryarchaeota;D_2__Methanobacteria;D_3__Methanobacteriales;D_4__Methanobacteriaceae;D_5__Methanobrevibacter;__  \
index                                                                                                                                       
387_Duo                                                  0                                                                                  
387_Sal                                                  0                                                                                  
388_Duo                                                  0                                                                                  
388_Sal                                                  0                                                                                  
390_Duo                                                  0                                                                                  
390_Sal                                                  0                                                                                  
391_Duo                                                  0                                                                                  
391_Sal                                                  0                                                                                  
392_Duo                                                  0                                                                                  
392_Sal                                                  0                                                                                  
409_Duo                                                  0                                                                                  
409_Sal                                                  0                                                                                  
410_Duo                                                  0                                                                                  
410_Sal                                                  0                                                                                  
417_Duo                                                  0                                                                                  
417_Sal                                                  0                                                                                  
418_Duo                                                  0                                                                                  
418_Sal                                                  0                                                                                  
423_Duo                                                  0                                                                                  
423_Sal                                                  0                                                                                  
425_Duo                                                  0                                                                                  
425_Sal                                                  0                                                                                  
433_Duo                                                  0                                                                                  
433_Sal                                                  0                                                                                  
434_Duo                                                  0                                                                                  
434_Sal                                                  0                                                                                  
437_Duo                                                  0   

### Set abundance to zero for taxa below LOD defined by # molecules input into amplification rxn or sequencing 50% CV threshold
This is defined as the load at which there should be a 95% chance of one copy being loaded into the amplification reaction (3 copy average).

In [14]:
df_species_lod_filter = pd.DataFrame()

for col in df_seq_samples.columns:
    df_species_lod_filter[col] = df_seq_samples.apply(lambda x: x[col] if x[col]>lod_dict[x.name] else 0, axis=1)
    
# Remove columns (taxa) that have zero counts after filtering
df_species_lod_filter = df_species_lod_filter[df_species_lod_filter.sum(axis=1)>0]

# Remove rows (samples) that have zero counts after filtering
df_species_lod_filter = df_species_lod_filter.loc[:, (df_species_lod_filter != 0).any(axis=0)]
df_species_lod_filter

D_0__Bacteria;D_1__Actinobacteria;D_2__Actinobacteria;D_3__Actinomycetales;D_4__Actinomycetaceae;D_5__F0332;D_6__uncultured bacterium  \
index                                                                                                                                            
387_Duo                                                  0                                                                                       
387_Sal                                                  0                                                                                       
388_Duo                                                  0                                                                                       
388_Sal                                                  0                                                                                       
390_Duo                                                  0                                                                                       
390_Sal                                                  0                                                                                       
391_Duo                                                  0                                                                                       
391_Sal                                                  0                                                                                       
392_Duo                                                  0                                                                                       
392_Sal                                                  0                                                                                       
409_Duo                                                  0                                                                                       
409_Sal                                                  0                                                                                       
410_Duo                                                  0                                                                                       
410_Sal                                                  0                                                                                       
417_Duo                                                  0                                                                                       
417_Sal                                                  0                                                                                       
418_Duo                                                  0                                                                                       
418_Sal                                                  0                                                                                       
423_Duo                                                  0                                                                                       
423_Sal                                                  0                                                                                       
425_Duo                                                  0                                                                                       
425_Sal                                                  0                                                                                       
433_Duo                                                  0                                                                                       
433_Sal                                                 24                                                                                       
434_Duo                                                  0                                                                                       
434_Sal                                                  0         

### Determine which samples (if any) were filtered out

In [15]:
orig_indexes = df_seq_samples.index.tolist()
filter_indexes = df_species_lod_filter.index.tolist()

lost = list(set(set(orig_indexes) - set(filter_indexes)))

In [16]:
df_total_load[df_total_load['Sample'].isin(lost)]

Empty DataFrame
Columns: [Well, Concentration, PoissonConfMax, PoissonConfMin, Total, Positives, Primer, Sample, Type, Dilution, Weight, Corrected Concentration, 16S Copies/g, mod_ID, Copies/mL, Log Copies/mL, Seq_Dilution, Copies in Amp Rxn, Rel. Abundance LOD (%), Abs. Abundance LOD, Rel. Abundance LOD (%) Corrected]
Index: []

[0 rows x 21 columns]

### Generate dataframes for each taxonomy level

In [17]:
def collapse_taxonomy(_df, level):
    collapsed_dict = {}
    index=0
    
    # Evaluate the selected taxonomy level to collapse to
    if level == 'Genus':
        index = -1
    elif level == 'Family':
        index = -2
    elif level == 'Order':
        index = -3
    elif level == 'Class':
        index = -4
    elif level == 'Phylum':
        index = -5
    else:
        raise ValueError('Could not interprest taxonomy level. Please use (Phylum, Class, Order, Family, Genus)')

    # Iterate through columns adding values together for each sample if the new column name already exists
    for col in _df:
        new_col = ";".join(col.split(';')[:index])

        if new_col in collapsed_dict.keys():
            collapsed_dict[new_col] += np.array(_df[col])
        else:
            collapsed_dict[new_col] = np.array(_df[col])

    df_collapsed = pd.DataFrame.from_dict(collapsed_dict).set_index(_df.index)
    return df_collapsed

In [18]:
df_lod_list = [None]*6

df_lod_list[0] = collapse_taxonomy(df_species_lod_filter, 'Phylum')
df_lod_list[1] = collapse_taxonomy(df_species_lod_filter, 'Class')
df_lod_list[2] = collapse_taxonomy(df_species_lod_filter, 'Order')
df_lod_list[3] = collapse_taxonomy(df_species_lod_filter, 'Family')
df_lod_list[4] = collapse_taxonomy(df_species_lod_filter, 'Genus')
df_lod_list[5] = df_species_lod_filter

### Generate relative and absolute abundance tables

In [19]:
df_rel_lod_list = [None]*6
df_abs_lod_list = [None]*6

df_pseudo_rel_lod_list = [None]*6
df_pseudo_abs_lod_list = [None]*6

for index, df in enumerate(df_lod_list):
    df_rel_lod_list[index] = df.div(read_depth, axis=0).multiply(100)
    df_abs_lod_list[index] = df_rel_lod_list[index].apply(lambda x: x*total_load_dict[x.name], 1).div(100)
    
    df_pseudo_rel_lod_list[index] = df_rel_lod_list[index]+(0.01/read_depth)*100
    df_pseudo_abs_lod_list[index] = df_pseudo_rel_lod_list[index].apply(lambda x: x*total_load_dict[x.name], 1).div(100)
    #df_pseudo_abs_lloq_list[index] = df_abs_lloq_list[index]+0.001

df_rel_lod_list[0]

D_0__Bacteria;D_1__Actinobacteria  D_0__Bacteria;D_1__Bacteroidetes  \
index                                                                          
387_Duo                           4.066299                          0.259551   
387_Sal                           5.047584                         13.530805   
388_Duo                           2.026319                         25.586267   
388_Sal                           8.606165                          9.821957   
390_Duo                           0.000000                         53.519876   
390_Sal                           4.371386                         22.765357   
391_Duo                           0.000000                          4.314467   
391_Sal                           1.675698                         27.389463   
392_Duo                           0.607896                         49.241838   
392_Sal                           1.746277                         20.481763   
409_Duo                           5.935522                          2.411092   
409_Sal                           1.092846                         46.359455   
410_Duo                          11.012704                          1.026820   
410_Sal                           1.427531                         40.943035   
417_Duo                           1.054141                         16.096717   
417_Sal                           0.498611                         25.984700   
418_Duo                           1.652930                          1.484450   
418_Sal                           0.801421                         21.836437   
423_Duo                           0.000000                         28.400346   
423_Sal                           1.120168                         45.883612   
425_Duo                           1.518601                         38.261008   
425_Sal                           1.161149                         44.132781   
433_Duo                           1.295478                          1.527708   
433_Sal                           3.378717                         12.474386   
434_Duo                           2.242612                          0.000000   
434_Sal                           9.022813                          2.190246   
437_Duo                           0.491781                         26.399071   
437_Sal                           0.594235                         42.605073   
438_Duo                           3.774874                          1.707573   
438_Sal                           5.268430                         10.138427   
441_Duo                           0.637494                          0.537316   
441_Sal                           1.247666                         10.024589   
446_Duo                           0.000000                         11.295023   
446_Sal                           0.910705                         34.226583   
447_Duo                           1.557306                          0.500888   
447_Sal                           1.509494                         24.142799   
448_Duo                           1.154319                         26.522016   
448_Sal                           2.183416                         45.312144   
449_Duo                           5.680525                          0.000000   
449_Sal                           3.501662                          9.075179   
451_Duo                           0.523656                          0.000000   
451_Sal                           0.598789                         29.040117   

         D_0__Bacteria;D_1__Epsilonbacteraeota  D_0__Bacteria;D_1__Firmicutes  \
index                                                                           
387_Duo                               0.000000                      91.191203   
387_Sal                               0.612449                      63.291744   
388_Duo                               0.020491                      23.238924   
388_Sal                               0.259551                      66.408633   
39

### Transform column taxa names into unique IDs.
This overcomes downstream issue when multiple columns have the same name

In [20]:
df_col_names_lod_list = [None]*6

for index, df in enumerate(df_rel_lod_list):
    num_cols = len(df.columns)
    col_names = ['ASV' + str(x) for x in range(num_cols)]
    df_col_names_lod_list[index] = pd.DataFrame(index=col_names, data={'taxonomy':df.columns.tolist()})
    
    df_rel_lod_list[index].columns = col_names
    df_abs_lod_list[index].columns = col_names
    
    df_pseudo_rel_lod_list[index].columns = col_names
    df_pseudo_abs_lod_list[index].columns = col_names
    
df_col_names_lod_list[0]

taxonomy
ASV0       D_0__Bacteria;D_1__Actinobacteria
ASV1        D_0__Bacteria;D_1__Bacteroidetes
ASV2   D_0__Bacteria;D_1__Epsilonbacteraeota
ASV3           D_0__Bacteria;D_1__Firmicutes
ASV4         D_0__Bacteria;D_1__Fusobacteria
ASV5      D_0__Bacteria;D_1__Patescibacteria
ASV6       D_0__Bacteria;D_1__Proteobacteria
ASV7         D_0__Bacteria;D_1__Spirochaetes
ASV8        D_0__Bacteria;D_1__Synergistetes
ASV9          D_0__Bacteria;D_1__Tenericutes
ASV10                       D_0__Bacteria;__

### Generate shorter taxonomy names for plotting purposes

In [21]:
exclusion_list = ['', 'uncultured bacterium', 'metagenome', 'uncultured', 
                  'gut metagenome', 'uncultured organism', 'unidentified', 
                  'uncultured Bacteroidales bacterium', 'uncultured Mollicutes bacterium', 'uncultured archaeon']

for i in range(6):
    if i == 0:
        df_col_names_lod_list[i][['Kingdom', 'Phylum']] = df_col_names_lod_list[i]['taxonomy'].str.split(';', expand=True)
    elif i==1:
        df_col_names_lod_list[i][['Kingdom', 'Phylum', 'Class']] = df_col_names_lod_list[i]['taxonomy'].str.split(';', expand=True)
    elif i==2:
        df_col_names_lod_list[i][['Kingdom', 'Phylum', 'Class', 'Order']] = df_col_names_lod_list[i]['taxonomy'].str.split(';', expand=True)
    elif i==3:
        df_col_names_lod_list[i][['Kingdom', 'Phylum', 'Class', 'Order', 'Family']] = df_col_names_lod_list[i]['taxonomy'].str.split(';', expand=True)
    elif i==4:
        df_col_names_lod_list[i][['Kingdom', 'Phylum', 'Class', 'Order', 'Family', 'Genus']] = df_col_names_lod_list[i]['taxonomy'].str.split(';', expand=True)
    else:
        df_col_names_lod_list[i][['Kingdom', 'Phylum', 'Class', 'Order', 'Family', 'Genus', 'Species']] = df_col_names_lod_list[i]['taxonomy'].str.split(';', expand=True)
        
    labels_list = []
    for index, row in df_col_names_lod_list[i].iterrows():
        # Species
        if row[-1][5:] in exclusion_list:
            # Genus
            if row[-2][5:] in exclusion_list:
                # Family
                if row[-3][5:] in exclusion_list:
                    # Order
                    if row[-4][5:] in exclusion_list:
                        # Class
                        if row[-5][5:] in exclusion_list:
                            # Phylum
                            if row[-6][5:] in exclusion_list:
                                labels_list.append(row[-7][5:] + '(' + df_col_names_lod_list[i].columns[-7][0].lower() + ')')
                            else:
                                labels_list.append(row[-6][5:] + '(' + df_col_names_lod_list[i].columns[-6][0].lower() + ')')
                        else:
                            labels_list.append(row[-5][5:] + '(' + df_col_names_lod_list[i].columns[-5][0].lower() + ')')
                    else:
                        labels_list.append(row[-4][5:] + '(' + df_col_names_lod_list[i].columns[-4][0].lower() + ')')
                else:
                    labels_list.append(row[-3][5:] + '(' + df_col_names_lod_list[i].columns[-3][0].lower() + ')')
            else:
                labels_list.append(row[-2][5:] + '(' + df_col_names_lod_list[i].columns[-2][0].lower() + ')')
        else:
            labels_list.append(row[-1][5:] + '(' + df_col_names_lod_list[i].columns[-1][0].lower() + ')')
                                   
    df_col_names_lod_list[i]['label'] = labels_list

### Sort the columns by the max abundance of taxa across all samples

In [22]:
df_rel_sort_lod_list = [None]*6
df_abs_sort_lod_list = [None]*6

df_pseudo_rel_sort_lod_list = [None]*6
df_pseudo_abs_sort_lod_list = [None]*6

for i in range(6):
    taxa_sorted = df_abs_lod_list[i].mean().sort_values(ascending=False).index
    
    df_rel_sort_lod_list[i] = df_rel_lod_list[i].loc[:, taxa_sorted]
    df_abs_sort_lod_list[i] = df_abs_lod_list[i].loc[:, taxa_sorted]
    
    df_pseudo_rel_sort_lod_list[i] = df_pseudo_rel_lod_list[i].loc[:, taxa_sorted]
    df_pseudo_abs_sort_lod_list[i] = df_pseudo_abs_lod_list[i].loc[:, taxa_sorted]
    
df_abs_sort_lod_list[4]

ASV13         ASV30         ASV68         ASV14         ASV94  \
index                                                                           
387_Duo  8.428612e+03  3.223476e+06  2.016311e+05  1.123815e+03  1.123815e+03   
387_Sal  5.563840e+07  3.814375e+08  4.369792e+07  2.660967e+07  4.592346e+07   
388_Duo  1.962599e+05  1.560678e+05  2.329590e+05  1.811232e+03  3.838087e+04   
388_Sal  1.553381e+07  8.815325e+07  1.491296e+07  1.531444e+05  1.574904e+07   
390_Duo  4.856886e+03  1.140589e+03  5.978206e+02  4.136448e+02  0.000000e+00   
390_Sal  1.180718e+08  3.266770e+08  3.677144e+07  9.685920e+06  1.850990e+07   
391_Duo  6.863924e+02  9.157815e+03  1.568742e+03  0.000000e+00  0.000000e+00   
391_Sal  1.026246e+07  1.963309e+07  4.272965e+06  1.464438e+06  2.638775e+06   
392_Duo  4.803707e+05  8.605142e+04  1.305731e+05  9.370915e+04  1.189618e+04   
392_Sal  7.730049e+07  2.872767e+08  2.344001e+07  1.558503e+07  3.231004e+07   
409_Duo  3.085864e+04  6.266752e+05  3.496561e+05  2.061537e+03  3.349998e+03   
409_Sal  1.556469e+09  8.546317e+08  4.929112e+08  1.484550e+08  7.385820e+07   
410_Duo  7.887939e+05  2.208983e+07  1.790454e+07  0.000000e+00  1.837277e+07   
410_Sal  1.066398e+09  3.892013e+08  8.557504e+08  1.164887e+08  7.361203e+07   
417_Duo  4.190950e+05  8.132215e+05  1.465893e+06  4.883625e+05  1.004110e+05   
417_Sal  2.250161e+07  1.614218e+08  7.043239e+07  3.446828e+07  8.254864e+07   
418_Duo  5.321134e+04  1.067898e+07  6.685096e+05  3.031026e+04  2.997348e+04   
418_Sal  2.009650e+07  1.095188e+08  1.690207e+07  2.017308e+07  6.265251e+07   
423_Duo  3.187431e+05  4.032560e+05  4.087727e+05  1.234363e+05  9.623589e+04   
423_Sal  1.635244e+09  8.786447e+08  6.239500e+08  1.989737e+08  1.649798e+08   
425_Duo  1.068859e+05  9.428495e+04  5.188428e+04  2.458499e+04  6.423846e+03   
425_Sal  3.146542e+08  3.050870e+08  1.449740e+08  2.619063e+08  1.294319e+08   
433_Duo  1.542153e+03  5.287257e+04  6.549785e+03  2.153195e+02  1.425764e+02   
433_Sal  5.627962e+07  2.884914e+08  9.717801e+07  1.308524e+07  2.919447e+07   
434_Duo  0.000000e+00  3.342736e+06  1.047206e+05  0.000000e+00  0.000000e+00   
434_Sal  6.854333e+05  9.114477e+07  2.842406e+07  1.306607e+06  0.000000e+00   
437_Duo  7.266069e+06  1.325150e+07  2.531533e+06  2.423676e+06  5.332087e+06   
437_Sal  4.511547e+08  3.315066e+08  1.086730e+08  1.583059e+08  1.158754e+08   
438_Duo  5.237379e+04  5.785044e+06  9.805444e+04  3.262904e+04  7.295518e+04   
438_Sal  9.086244e+06  2.234501e+08  3.982426e+07  1.091744e+07  0.000000e+00   
441_Duo  3.701055e+03  2.971595e+06  1.414332e+05  8.107073e+03  1.462798e+04   
441_Sal  5.377132e+06  1.414318e+08  1.763170e+07  1.178808e+07  1.623856e+07   
446_Duo  3.792437e+04  3.187469e+05  6.220443e+04  1.797017e+04  1.406715e+04   
446_Sal  9.599705e+07  8.519352e+07  6.910000e+07  3.573147e+07  5.536940e+07   
447_Duo  5.764132e+04  8.640405e+06  7.843855e+05  2.896549e+03  2.519998e+04   
447_Sal  5.505671e+07  8.792650e+07  7.434590e+07  8.448397e+06  1.682573e+07   
448_Duo  9.553171e+05  1.602201e+06  4.853126e+05  1.026117e+05  3.581841e+05   
448_Sal  5.252247e+08  3.587311e+08  2.005168e+08  1.025008e+08  8.512263e+07   
449_Duo  0.000000e+00  4.338810e+05  3.106546e+03  0.000000e+00  8.487392e+04   
449_Sal  4.491326e+06  1.739948e+08  7.749738e+06  1.061186e+07  2.613335e+07   
451_Duo  0.000000e+00  3.012703e+08  3.935602e+06  0.000000e+00  5.356791e+05   
451_Sal  4.356429e+07  1.504739e+08  2.412288e+07  1.605766e+07  2.111510e+07   

                ASV87         ASV12         ASV70         ASV23         ASV71  \
index                                                                           
387_Duo  0.000000e+00  0.000000e+00  7.773054e+03  7.192416e+04  1.696961e+05   
387_Sal  1.201790e+07  1.273394e+07  9.753654e+06  2.734507e+07  7.984837e+07   
388_Duo  5.675194e+04  7.805548e+03  2.078605e+04  1.241988e+04  6.007254e+04   
388_Sal  8.514003e+06  1.618364e+06  6.374120e

### Save the working files to allow use in individual analysis workbooks

In [24]:
pickle.dump(df_rel_sort_lod_list, open('pickle_files/rel_sort_lod_list_paired.pkl', 'wb'))
pickle.dump(df_abs_sort_lod_list, open('pickle_files/abs_sort_lod_list_paired.pkl', 'wb'))

pickle.dump(df_pseudo_rel_sort_lod_list, open('pickle_files/pseudo_rel_sort_lod_list_paired.pkl', 'wb'))
pickle.dump(df_pseudo_abs_sort_lod_list, open('pickle_files/pseudo_abs_sort_lod_list_paired.pkl', 'wb'))

pickle.dump(df_col_names_lod_list, open('pickle_files/col_names_lod_list_paired.pkl', 'wb'))
pickle.dump(df_total_load, open('pickle_files/total_load_paired.pkl', 'wb'))
pickle.dump(seq_metadata, open('pickle_files/seq_paired_metadata_paired.pkl', 'wb'))